# Exporatory Analytics of Dataset

## DS 5110
* Fall 2021
* October 3rd
* Group 10
  * Antone Edelman
  * Xin Huang
  * Robert Knuuti

In [1]:
from pyspark.sql import SparkSession
import pyspark.sql.functions as F
import pyspark.sql.types as T

import pandas as pd
import numpy as np

spark = SparkSession.builder \
    .master("local[*]") \
    .appName("fa21-ds5110-group10") \
    .getOrCreate()

df = spark.read.parquet("../../data/processed/chess_games_blitz_classic.parquet")

In [3]:
spark

There's some additional cleanup we have to do beyond the filtering of games to just classic and blitz.
Below are our transforms to add new features and to transform the data.

In [2]:
df.printSchema()

print("Abandoned Games to drop: {}".format(df.filter(df.result.contains("*")).count()))
# Remove all abandoned games.
df_filtered = df.filter(~df.result.contains("*"))

from fractions import Fraction as frac

# Convert result column into seperate white/black win columns
white_win_udf = F.udf(lambda result: float(frac(result.split('-')[0])), T.DoubleType())
black_win_udf = F.udf(lambda result: float(frac(result.split('-')[1])), T.DoubleType())

# We break apar the AN notation for chess moves into arrays
def movetype(x):
    import re
    moves = re.split('\d+\. ', x)[1:]
    return [x.strip() for x in moves]

# We establish a bin rate to determine the complexity of a match (based on number of moves)
def bin_moves(x):
    if x == 1:
        return 1
    elif x <= 10:
        return 2
    elif x <= 20:
        return 3
    elif x <= 30:
        return 4
    elif x <= 40:
        return 5
    elif x <= 50:
        return 6
    else:
        return 7

udf_movetype = F.udf(lambda x: movetype(x), T.ArrayType(T.StringType()))
df_filtered = df_filtered.withColumn('moves', udf_movetype(F.col('AN')))

# Calculate the total number of moves in a game
count_udf  = F.udf(lambda result: len(result), T.IntegerType())
game_complexity_udf = F.udf(lambda result: bin_moves(result), T.IntegerType())

df_filtered = df_filtered.withColumn("white_games_won", white_win_udf(df_filtered.result))
df_filtered = df_filtered.withColumn("black_games_won", black_win_udf(df_filtered.result))
df_filtered = df_filtered.withColumn("tie", df_filtered.white_games_won == df_filtered.black_games_won)
df_filtered = df_filtered.withColumn("result_moves", count_udf(df_filtered.moves))
df_filtered = df_filtered.withColumn("game_complexity", game_complexity_udf(df_filtered.result_moves))

print("Refined schema\n-------------------")
df_filtered.printSchema()

df_to_save = df_filtered.drop()

root
 |-- event: string (nullable = true)
 |-- white: string (nullable = true)
 |-- black: string (nullable = true)
 |-- result: string (nullable = true)
 |-- UTCDate: date (nullable = true)
 |-- UTCTime: string (nullable = true)
 |-- WhiteElo: integer (nullable = true)
 |-- BlackElo: integer (nullable = true)
 |-- WhiteRatingDiff: double (nullable = true)
 |-- BlackRatingDiff: double (nullable = true)
 |-- ECO: string (nullable = true)
 |-- Opening: string (nullable = true)
 |-- TimeControl: string (nullable = true)
 |-- Termination: string (nullable = true)
 |-- AN: string (nullable = true)

Abandoned Games to drop: 739
Refined schema
-------------------
root
 |-- event: string (nullable = true)
 |-- white: string (nullable = true)
 |-- black: string (nullable = true)
 |-- result: string (nullable = true)
 |-- UTCDate: date (nullable = true)
 |-- UTCTime: string (nullable = true)
 |-- WhiteElo: integer (nullable = true)
 |-- BlackElo: integer (nullable = true)
 |-- WhiteRatingDiff: d

In [4]:
df_filtered.write.format("parquet").save("../../data/processed/chess_games_moves.parquet")

ERROR:py4j.java_gateway:An error occurred while trying to connect to the Java server (127.0.0.1:38811)
Traceback (most recent call last):
  File "/opt/conda/lib/python3.7/site-packages/IPython/core/interactiveshell.py", line 3441, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-4-9c1a5d942153>", line 1, in <module>
    df_filtered.write.format("parquet").save("../../data/processed/chess_games_moves.parquet")
  File "/usr/local/spark/python/pyspark/sql/readwriter.py", line 1109, in save
    self._jwrite.save(path)
  File "/usr/local/spark/python/lib/py4j-0.10.9-src.zip/py4j/java_gateway.py", line 1305, in __call__
    answer, self.gateway_client, self.target_id, self.name)
  File "/usr/local/spark/python/pyspark/sql/utils.py", line 111, in deco
    return f(*a, **kw)
  File "/usr/local/spark/python/lib/py4j-0.10.9-src.zip/py4j/protocol.py", line 328, in get_return_value
    format(target_id, ".", name), value)
py4j.protocol.Py4JJavaError: <unprin

ERROR:py4j.java_gateway:An error occurred while trying to connect to the Java server (127.0.0.1:38811)
Traceback (most recent call last):
  File "/opt/conda/lib/python3.7/site-packages/IPython/core/interactiveshell.py", line 3441, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-4-9c1a5d942153>", line 1, in <module>
    df_filtered.write.format("parquet").save("../../data/processed/chess_games_moves.parquet")
  File "/usr/local/spark/python/pyspark/sql/readwriter.py", line 1109, in save
    self._jwrite.save(path)
  File "/usr/local/spark/python/lib/py4j-0.10.9-src.zip/py4j/java_gateway.py", line 1305, in __call__
    answer, self.gateway_client, self.target_id, self.name)
  File "/usr/local/spark/python/pyspark/sql/utils.py", line 111, in deco
    return f(*a, **kw)
  File "/usr/local/spark/python/lib/py4j-0.10.9-src.zip/py4j/protocol.py", line 328, in get_return_value
    format(target_id, ".", name), value)
py4j.protocol.Py4JJavaError: <unprin

ERROR:py4j.java_gateway:An error occurred while trying to connect to the Java server (127.0.0.1:38811)
Traceback (most recent call last):
  File "/opt/conda/lib/python3.7/site-packages/IPython/core/interactiveshell.py", line 3441, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-4-9c1a5d942153>", line 1, in <module>
    df_filtered.write.format("parquet").save("../../data/processed/chess_games_moves.parquet")
  File "/usr/local/spark/python/pyspark/sql/readwriter.py", line 1109, in save
    self._jwrite.save(path)
  File "/usr/local/spark/python/lib/py4j-0.10.9-src.zip/py4j/java_gateway.py", line 1305, in __call__
    answer, self.gateway_client, self.target_id, self.name)
  File "/usr/local/spark/python/pyspark/sql/utils.py", line 111, in deco
    return f(*a, **kw)
  File "/usr/local/spark/python/lib/py4j-0.10.9-src.zip/py4j/protocol.py", line 328, in get_return_value
    format(target_id, ".", name), value)
py4j.protocol.Py4JJavaError: <unprin

ERROR:py4j.java_gateway:An error occurred while trying to connect to the Java server (127.0.0.1:38811)
Traceback (most recent call last):
  File "/opt/conda/lib/python3.7/site-packages/IPython/core/interactiveshell.py", line 3441, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-4-9c1a5d942153>", line 1, in <module>
    df_filtered.write.format("parquet").save("../../data/processed/chess_games_moves.parquet")
  File "/usr/local/spark/python/pyspark/sql/readwriter.py", line 1109, in save
    self._jwrite.save(path)
  File "/usr/local/spark/python/lib/py4j-0.10.9-src.zip/py4j/java_gateway.py", line 1305, in __call__
    answer, self.gateway_client, self.target_id, self.name)
  File "/usr/local/spark/python/pyspark/sql/utils.py", line 111, in deco
    return f(*a, **kw)
  File "/usr/local/spark/python/lib/py4j-0.10.9-src.zip/py4j/protocol.py", line 328, in get_return_value
    format(target_id, ".", name), value)
py4j.protocol.Py4JJavaError: <unprin

ERROR:py4j.java_gateway:An error occurred while trying to connect to the Java server (127.0.0.1:38811)
Traceback (most recent call last):
  File "/opt/conda/lib/python3.7/site-packages/IPython/core/interactiveshell.py", line 3441, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-4-9c1a5d942153>", line 1, in <module>
    df_filtered.write.format("parquet").save("../../data/processed/chess_games_moves.parquet")
  File "/usr/local/spark/python/pyspark/sql/readwriter.py", line 1109, in save
    self._jwrite.save(path)
  File "/usr/local/spark/python/lib/py4j-0.10.9-src.zip/py4j/java_gateway.py", line 1305, in __call__
    answer, self.gateway_client, self.target_id, self.name)
  File "/usr/local/spark/python/pyspark/sql/utils.py", line 111, in deco
    return f(*a, **kw)
  File "/usr/local/spark/python/lib/py4j-0.10.9-src.zip/py4j/protocol.py", line 328, in get_return_value
    format(target_id, ".", name), value)
py4j.protocol.Py4JJavaError: <unprin

...

ERROR:py4j.java_gateway:An error occurred while trying to connect to the Java server (127.0.0.1:38811)
Traceback (most recent call last):
  File "/opt/conda/lib/python3.7/site-packages/IPython/core/interactiveshell.py", line 3441, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-4-9c1a5d942153>", line 1, in <module>
    df_filtered.write.format("parquet").save("../../data/processed/chess_games_moves.parquet")
  File "/usr/local/spark/python/pyspark/sql/readwriter.py", line 1109, in save
    self._jwrite.save(path)
  File "/usr/local/spark/python/lib/py4j-0.10.9-src.zip/py4j/java_gateway.py", line 1305, in __call__
    answer, self.gateway_client, self.target_id, self.name)
  File "/usr/local/spark/python/pyspark/sql/utils.py", line 111, in deco
    return f(*a, **kw)
  File "/usr/local/spark/python/lib/py4j-0.10.9-src.zip/py4j/protocol.py", line 328, in get_return_value
    format(target_id, ".", name), value)
py4j.protocol.Py4JJavaError: <unprin

ERROR:py4j.java_gateway:An error occurred while trying to connect to the Java server (127.0.0.1:38811)
Traceback (most recent call last):
  File "/opt/conda/lib/python3.7/site-packages/IPython/core/interactiveshell.py", line 3441, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-4-9c1a5d942153>", line 1, in <module>
    df_filtered.write.format("parquet").save("../../data/processed/chess_games_moves.parquet")
  File "/usr/local/spark/python/pyspark/sql/readwriter.py", line 1109, in save
    self._jwrite.save(path)
  File "/usr/local/spark/python/lib/py4j-0.10.9-src.zip/py4j/java_gateway.py", line 1305, in __call__
    answer, self.gateway_client, self.target_id, self.name)
  File "/usr/local/spark/python/pyspark/sql/utils.py", line 111, in deco
    return f(*a, **kw)
  File "/usr/local/spark/python/lib/py4j-0.10.9-src.zip/py4j/protocol.py", line 328, in get_return_value
    format(target_id, ".", name), value)
py4j.protocol.Py4JJavaError: <unprin

ERROR:py4j.java_gateway:An error occurred while trying to connect to the Java server (127.0.0.1:38811)
Traceback (most recent call last):
  File "/opt/conda/lib/python3.7/site-packages/IPython/core/interactiveshell.py", line 3441, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-4-9c1a5d942153>", line 1, in <module>
    df_filtered.write.format("parquet").save("../../data/processed/chess_games_moves.parquet")
  File "/usr/local/spark/python/pyspark/sql/readwriter.py", line 1109, in save
    self._jwrite.save(path)
  File "/usr/local/spark/python/lib/py4j-0.10.9-src.zip/py4j/java_gateway.py", line 1305, in __call__
    answer, self.gateway_client, self.target_id, self.name)
  File "/usr/local/spark/python/pyspark/sql/utils.py", line 111, in deco
    return f(*a, **kw)
  File "/usr/local/spark/python/lib/py4j-0.10.9-src.zip/py4j/protocol.py", line 328, in get_return_value
    format(target_id, ".", name), value)
py4j.protocol.Py4JJavaError: <unprin

ERROR:py4j.java_gateway:An error occurred while trying to connect to the Java server (127.0.0.1:38811)
Traceback (most recent call last):
  File "/opt/conda/lib/python3.7/site-packages/IPython/core/interactiveshell.py", line 3441, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "<ipython-input-4-9c1a5d942153>", line 1, in <module>
    df_filtered.write.format("parquet").save("../../data/processed/chess_games_moves.parquet")
  File "/usr/local/spark/python/pyspark/sql/readwriter.py", line 1109, in save
    self._jwrite.save(path)
  File "/usr/local/spark/python/lib/py4j-0.10.9-src.zip/py4j/java_gateway.py", line 1305, in __call__
    answer, self.gateway_client, self.target_id, self.name)
  File "/usr/local/spark/python/pyspark/sql/utils.py", line 111, in deco
    return f(*a, **kw)
  File "/usr/local/spark/python/lib/py4j-0.10.9-src.zip/py4j/protocol.py", line 328, in get_return_value
    format(target_id, ".", name), value)
py4j.protocol.Py4JJavaError: <unprin

Py4JNetworkError: An error occurred while trying to connect to the Java server (127.0.0.1:38811)

## Number of records

In [ ]:
print(f"Total number of records are: {df.count()}")

Reviewing our dataset, we found that games which were abandoned had a value of "\*" for the results.
Given the total number of abandonded records are small in comparison to the others, we chose to drop these from our dataset.


In [ ]:
print("Total records: {}".format(df_filtered.count()))

## Number of columns

In [ ]:
print(f"Total number of columns are: {len(df_filtered.columns)}")

## Statistical Summary of Response Variable

In [ ]:
df_filtered.select(["white_games_won", "black_games_won"]).describe().show()

## Statistical summary of potential predictor variables (if there are a large number of predictors, select the top 10)

*Note*: Summarize categorical variables with counts and percentages for each level and summarize numerical variables with mean/quantiles/standard deviation.

In [ ]:
df_filtered.select(["WhiteElo", "BlackElo", "result_moves", "game_complexity", "ECO", "TimeControl"]).describe().show()

## Include up to five helpful graphs

In [7]:
import matplotlib.pyplot as plt
import pandas as pd
%matplotlib inline

df_games_per_date = df_filtered.groupBy(["UTCDate"]).count().sort("UTCDate")

ERROR:py4j.java_gateway:An error occurred while trying to connect to the Java server (127.0.0.1:44288)
Traceback (most recent call last):
  File "/usr/local/spark/python/lib/py4j-0.10.9-src.zip/py4j/java_gateway.py", line 977, in _get_connection
    connection = self.deque.pop()
IndexError: pop from an empty deque

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/usr/local/spark/python/lib/py4j-0.10.9-src.zip/py4j/java_gateway.py", line 1115, in start
    self.socket.connect((self.address, self.port))
ConnectionRefusedError: [Errno 111] Connection refused
ERROR:py4j.java_gateway:An error occurred while trying to connect to the Java server (127.0.0.1:44288)
Traceback (most recent call last):
  File "/usr/local/spark/python/lib/py4j-0.10.9-src.zip/py4j/java_gateway.py", line 977, in _get_connection
    connection = self.deque.pop()
IndexError: pop from an empty deque

During handling of the above exception, another exception

Py4JNetworkError: An error occurred while trying to connect to the Java server (127.0.0.1:44288)

In [ ]:
df_games_per_date.show(31)
df_pandas = df_games_per_date.toPandas()
plt.plot(df_pandas['UTCDate'], df_pandas['count'])
plt.xticks(rotation=90)
plt.xlabel("Date")
plt.ylabel("Games")
plt.title("Events per Day")

In [ ]:
moves_count = df_filtered.select('result_moves').toPandas()

plt.violinplot(moves_count,
               showmeans=False,
               showmedians=True)
plt.ylim(0,115) #Note there are outliers beyond 100 moves; to be filtered in future transforms.
plt.xlabel("Density")
plt.ylabel("Number of Moves")
plt.title("Events per Day")

In [6]:
def label_wins(x):
    if x == 0.0:
        return 'loss'
    elif x == 0.5:
        return 'tie'
    else:
        return 'win'

white_wins = df_filtered.groupBy('white_games_won').count().toPandas()
white_wins['white_games_won'] = white_wins['white_games_won'].apply(label_wins)

display(white_wins)
plt.bar(x=white_wins['white_games_won'], height=white_wins['count'])
plt.xlabel("White Game Result")
plt.ylabel("Number of Games")
plt.title("Game Result Summary for White")

ERROR:py4j.java_gateway:An error occurred while trying to connect to the Java server (127.0.0.1:44288)
Traceback (most recent call last):
  File "/usr/local/spark/python/lib/py4j-0.10.9-src.zip/py4j/java_gateway.py", line 977, in _get_connection
    connection = self.deque.pop()
IndexError: pop from an empty deque

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/usr/local/spark/python/lib/py4j-0.10.9-src.zip/py4j/java_gateway.py", line 1115, in start
    self.socket.connect((self.address, self.port))
ConnectionRefusedError: [Errno 111] Connection refused


Py4JNetworkError: An error occurred while trying to connect to the Java server (127.0.0.1:44288)

In [ ]:
binned_moves = df_filtered.groupBy('game_complexity').count().toPandas()

plt.bar(x=[1,2,3,4,5,6,7], height=binned_moves['count'])
plt.xlabel("Game Complexity")
plt.ylabel("Number of Games")
plt.title("Complexity of Games by Count")